In [1]:
import pandas as pd
from IPython.display import clear_output, Markdown, Math
import ipywidgets as widgets
import os
import glob
import json
import numpy as np
import itertools
import sklearn.utils as sku
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer, HashingVectorizer
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MultiLabelBinarizer

In [32]:
import sys
sys.path.append("..")

from Tools.Emoji_Distance import sentiment_vector_to_emoji
from Tools.Emoji_Distance import emoji_to_sentiment_vector

def emoji2sent(emoji_arr):
    return np.array([emoji_to_sentiment_vector(e) for e in emoji_arr])

def sent2emoji(sent_arr, custom_target_emojis=None):
    return [sentiment_vector_to_emoji(s, custom_target_emojis=custom_target_emojis) for s in sent_arr]

In [3]:
SINGLE_LABEL = True

# simple twitter approach
*for learning emoji usage by single (in the meaning of unconnected) twitter messages*

## loading train data

In [4]:
data_root_folder = "./data_en/" # i created a symlink here

* get all json files in `data_root_folder`

In [5]:
json_files = sorted(glob.glob(data_root_folder + "/*.json"))

----

* so far, only load the first file

In [6]:
twitter_data = pd.read_json(json_files[0], encoding="utf-8")
twitter_data

EMOJI  \
0                           [🔥, 👏]   
1                              [🤦]   
2                              [😄]   
3                              [📷]   
4                           [😩, 😩]   
5                           [😭, 💓]   
6                              [😂]   
7                              [💯]   
8                              [🙄]   
9                        [😟, 😥, 😢]   
10                             [🌻]   
11                       [🍁, 🌺, 🍂]   
12                             [🍃]   
13                          [💭, 🤦]   
14                          [😍, 😘]   
15                             [😜]   
16                          [😂, 🔥]   
17                             [💕]   
18                             [😉]   
19                             [👅]   
20                          [👌, 🙂]   
21                          [🤗, 📺]   
22                             [💯]   
23                       [👅, 💦, 🍑]   
24                             [💔]   
25                       [🤐, 🤐, 🤐]   
26                             [😴]   
27                             [😂]   
28                          [😂, 🙄]   
29              [🎉, 🎂, 🎈, 🎊, 🎁, 💜]   
...                            ...   
68703                          [😕]   
68704                       [😂, 😩]   
68705                          [😂]   
68706                          [💖]   
68707                 [🌆, 👉, 🚖, 📞]   
68708                          [😁]   
68709                          [😋]   
68710                    [👌, 🎃, 😘]   
68711                          [👍]   
68712                          [😭]   
68713                          [😂]   
68714                    [😭, 😭, 💘]   
68715                       [😫, ✋]   
68716                       [😂, 🙁]   
68717                          [😭]   
68718                       [😢, 💔]   
68719                          [🙃]   
68720              [😂, 😂, 😂, 😂, 😂]   
68721                    [👌, 👊, 🙌]   
68722                          [😴]   
68723                 [😂, 😂, 😂, 😂]   
68724                          [😀]   
68725                          [😎]   
68726                          [✨]   
68727                          [🤷]   
68728                          [😘]   
68729                          [😂]   
68730                          [🙏]   
68731                          [💁]   
68732  [🍃, 🌻, 🌻, 🍃, 🍃, 💐, 💐, 🍃, 🙋]   

                                              HASHTAGS  \
0                                                   []   
1                                                   []   
2                                                   []   
3                                                   []   
4                                                   []   
5                                                   []   
6                                                   []   
7                                                   []   
8                                                   []   
9                                                   []   
10                                                  []   
11                                                  []   
12         [#mortdale, #partofthefamily, #gorgeousboy]   
13                                                  []   
14                                     [#7YearsOfKMH2]   
15                                                  []   
16                                                  []   
17                                                  []   
18                                                  []   
19                                 [#footfetishnation]   
20                                                  []   
21                                                  []   
22                                                  []   
23                                                  []   
24                                                  []   
25                                                  []   
26                                                  []   
27                                              

* extracting emojis and text

In [7]:
emojis = twitter_data['EMOJI']
plain_text = twitter_data['text']

* make our plain text more "plain":
    * removing the keyword `<EMOJI>` (just for the beginning)
    * removing remaining useless emojis, like skin modifier etc.

In [8]:
# defining blacklist for modifier emojis:
emoji_blacklist = set([
    chr(0x1F3FB),
    chr(0x1F3FC),
    chr(0x1F3FD),
    chr(0x1F3FE),
    chr(0x1F3FF),
    chr(0x2642),
    chr(0x2640)
])

In [9]:
# filtering them and the EMOJI keyword out:
plain_text = plain_text.str.replace("(<EMOJI>|<USER>|<HASHTAG>)","").str.replace("[" + "".join(list(emoji_blacklist)) + "]","")

* defining different criterias for choosing a single emoji (currently `latest` is used)

In [10]:
def latest(lst):
    return lst[-1] if len(lst) > 0 else 'X' 
def most_common(lst):
    # trying to find the most common used emoji in the given lst
    return max(set(lst), key=lst.count) if len(lst) > 0 else "X" # setting label to 'X' if there is an empty emoji list

* convert all emojis to a sentiment vector

In [11]:
labels = emoji2sent([latest(e) for e in emojis])


In [12]:
len(labels)

68733

In [13]:
wrong_labels = np.isnan(np.linalg.norm(labels, axis=1))

* remove all data we have no label for

In [14]:
labels = labels[np.invert(wrong_labels)]
plain_text = plain_text[np.invert(wrong_labels)]
emojis = emojis[np.invert(wrong_labels)]

In [15]:
print(len(labels), len(emojis), len(plain_text))

33368 33368 33368


* generate weights:

In [16]:
# at first count over our table
emoji_count = {}


for e_list in emojis:
    for e in set(e_list):
        if e not in emoji_count:
            emoji_count[e] = 0
        emoji_count[e] += 1

emoji_count
emoji_sum = sum([emoji_count[e] for e in emoji_count])

emoji_weights = {}
for e in emoji_count:
    # tfidf for emojis
    emoji_weights[e] = np.log((emoji_sum / emoji_count[e]))

weights_sum= sum([emoji_weights[x] for x in emoji_weights])
    
# normalize:
for e in emoji_weights:
    emoji_weights[e] = emoji_weights[e] / weights_sum

emoji_weights['X'] = 0  # dummy values
emoji_count['X'] = 0

* most used emojis in Dataset

In [17]:
import operator

In [18]:
sorted_emoji_count = list(reversed(sorted(emoji_count.items(), key=operator.itemgetter(1))))
display(sorted_emoji_count[:20])

top_emojis = [x[0] for x in sorted_emoji_count[:20]]
display(top_emojis)

[('😂', 10182),
 ('😭', 3893),
 ('😍', 2866),
 ('😩', 1647),
 ('😊', 1450),
 ('😘', 1151),
 ('🙏', 1089),
 ('🙌', 1003),
 ('😉', 752),
 ('😁', 697),
 ('😅', 651),
 ('😎', 606),
 ('😢', 544),
 ('😒', 539),
 ('😏', 478),
 ('😌', 434),
 ('😔', 415),
 ('😋', 397),
 ('😀', 392),
 ('😤', 368)]

['😂',
 '😭',
 '😍',
 '😩',
 '😊',
 '😘',
 '🙏',
 '🙌',
 '😉',
 '😁',
 '😅',
 '😎',
 '😢',
 '😒',
 '😏',
 '😌',
 '😔',
 '😋',
 '😀',
 '😤']

* only learn the most used ones:

In [19]:
in_top = [sentiment_vector_to_emoji(x) in top_emojis for x in labels]
labels = labels[in_top]
plain_text = plain_text[in_top]
emojis = emojis[in_top]
print(len(labels), len(emojis), len(plain_text))

26197 26197 26197


* generating train and test set:

In [20]:
X1, Xt1, y1, yt1 = train_test_split(plain_text, labels, test_size=0.1, random_state=4222)

In [21]:
#y1_weights = np.array([(sum([emoji_weights[e] for e in e_list]) / len(e_list)) if len(e_list) > 0 else 0 for e_list in sent2emoji(y1)])

In [22]:
vectorizer = TfidfVectorizer(stop_words='english')
vec_train = vectorizer.fit_transform(X1)
vec_test = vectorizer.transform(Xt1)

* train. this can take a very long time...

In [23]:
from sklearn.neural_network import MLPClassifier as MLP
from sklearn.multiclass import OneVsRestClassifier as OVRC
from sklearn.tree import DecisionTreeClassifier as DTC

from keras.models import Sequential
from keras.layers import Dense

Using TensorFlow backend.


In [24]:
def train(max_size = 10000, layers=[(1024, 'relu'),(y1[0].shape[0],'softmax')], random_state=4222, ovrc=False, n_iter=5):
    
    model = Sequential()
    
    # build mlp layers:
    keras_layers = []
    first_layer = True
    for layer in layers:
        if first_layer:
            model.add(Dense(units=layer[0], activation=layer[1], input_dim=vectorizer.transform([" "])[0]._shape[1]))
            first_layer = False
        else:
            model.add(Dense(units=layer[0], activation=layer[1]))
    
    #mlp = MLPClassifier(layers=sknn_layers, random_state=random_state, verbose=True, n_iter=n_iter, batch_size=100)
    
    model.compile(loss='mean_squared_error',
              optimizer='adam')
    
    clf = OVRC(model) if ovrc else model

    clf.fit(vec_train[:max_size].A, y1[:max_size], validation_split=0.2, epochs=n_iter)#, sample_weight=y1_weights[:max_size])
    
    return clf

In [25]:
clf = train(max_size=100000,layers=[(10000, 'relu'),(5000, 'relu'),(2500, 'relu'),(y1[0].shape[0],None)], n_iter=3)

Train on 18861 samples, validate on 4716 samples
Epoch 1/3
18861/18861 [==============================] - 1288s 68ms/step - loss: 0.0185 - val_loss: 0.0164
Epoch 2/3
18861/18861 [==============================] - 1282s 68ms/step - loss: 0.0103 - val_loss: 0.0164
Epoch 3/3
18861/18861 [==============================] - 1333s 71ms/step - loss: 0.0063 - val_loss: 0.0166


* make a prediction and store it in a csv file:

In [26]:
pred = clf.predict(vectorizer.transform(Xt1))

In [27]:
print(np.linalg.norm(np.var(pred, axis=0)))
print(np.linalg.norm(np.var(labels, axis=0)))


0.012647177
0.03387511671001757


In [33]:
# build a dataframe to visualize test results:
testlist = pd.DataFrame({'text': Xt1, 
                         'teacher': sent2emoji(yt1),
                         'teacher_sentiment': yt1.tolist(),
                         'predict': sent2emoji(pred, custom_target_emojis=top_emojis),
                         'predicted_sentiment': pred.tolist()})

In [34]:
display(testlist)


text teacher  \
35671  I feel like I care so much more in every situa...       😂   
25683  I did not meat to add that '2' there...havent ...       😂   
8985                                           never…          😊   
5410          Lmao on me!!! Wtf was he supposed to say         😂   
62611   This dude always help me get through my schoo...       😊   
48197                                   Happy B'Day  Sir       😊   
23654     You need some good old fashioned Swedish Jesus       🙏   
58207  these late shifts are making me not have a soc...       😅   
374                                     Dc this weekend        😍   
26310                     Paul lad you'll make es blush        😊   
30892                      Did you have a fun Halloween?       😂   
11868                                    Hi handsome           😍   
46219       I'm not okay with this, I'm suing Snapchat         😭   
13583  My parents be so mad I be buying new stuff &am...       😭   
43843  One of the few songs that calms me down esp on...       😂   
63589      iPhone X Bouta Be The Last Phone We Ever Buy        😂   
53695         Visited my main man today ❤ i miss u papa        😭   
67529                                          Donuts          😍   
25493  Has anyone heard this  by  ? Who the fuck knew...       😘   
19486                                      Wow  superrbb       😍   
48449      Of course they don't. Their perfect model ...       😂   
4504          Please pick me. Pick me. Pick me. Please.        😍   
40285                             shiid no crack is wack       😭   
56741                    Pj still sleeps like a newborn        😩   
22948   An opinion doesn't mean you make sense first ...       😌   
68426                                       Missyou too        😘   
13431                                  I swear she did         😩   
66287        It’s true, he was the mutt’s (big-d) nuts.        😉   
41980                             is happening  so happy       😭   
34632   Saw that the first one said sosee you tmmrw a...       😂   
...                                                  ...     ...   
47218                           Keep it I don't want it        😂   
35087  6 years ago today we said our final good byes ...       😢   
61252                                              amen        🙏   
39960                                              FACT        😎   
365                   nw Finally Found Someone Hi Loydi        😅   
50665                      I need ur shoulder to cry on        😢   
21007               awww you'll get me teary eyed gurl!        😘   
18819  〰Happy Hump Day to all my  Ladies   is def swe...       😘   
42421                                           Thanks.        😊   
38705   its okay I didn’t see you until I was in your...       😂   
47033            Fall in  with    alexissdanger  ⬅️            😍   
38742                  Let your wild side free girl!!!!!       😂   
67610                      Can we get season 3 already!?       😭   
61021      Have to quote this bih  remember this nigga         😂   
14904                                      He so  damn         😩   
50994   YASSS It's time for a great show Maxloyal™♛:G...       😂   
6973                   Got to love a fish finger sarnie        😂   
3269                                            say dat        😂   
54827                             If ur happy I'm happy        😊   
19409                                        Rockstar          😀   
38703               God fuck me I already fixed it once        😂   
25133   It’s socially acceptable to listen to ANY Chr...       😂   
15339   I thrashed p in iMessage now he wanna bet on 2k        😂   
28082  my fatass need some lemon pepper wings w a lil...       😂   
44462    fck off tristan yes soph collect u in 15 n w...       😤   
60212                                     Open the bag         😋   
34950  I asked people to guess my zodiac sign and thi...       😤   
59462                                 I 

In [35]:
testlist.to_csv('test.csv')

* save classifier:

In [36]:
import pickle
clf.save("clf.keras")
pickle.dump( vectorizer, open( "vec.pickle", "wb" ) )

----
## testing area

**for just testing, start from here!**

* loading classifier and vectorizer

In [5]:
from IPython.display import clear_output, Markdown, Math
import ipywidgets as widgets
import sys
sys.path.append("..")

from Tools.Emoji_Distance import sentiment_vector_to_emoji
from Tools.Emoji_Distance import emoji_to_sentiment_vector

def emoji2sent(emoji_arr):
    return np.array([emoji_to_sentiment_vector(e) for e in emoji_arr])

def sent2emoji(sent_arr, custom_target_emojis=None):
    return [sentiment_vector_to_emoji(s, custom_target_emojis=custom_target_emojis) for s in sent_arr]

In [2]:
import keras
import pickle
clf = keras.models.load_model("clf.keras")
vectorizer = pickle.load( open( "vec.pickle", "rb" ) )

Using TensorFlow backend.


* define lookup emojis here:

In [8]:
lookup_emojis = ['😭', '😍', '😩', '😊']

* a simple output widget for testing:

In [9]:
out = widgets.Output()

t = widgets.Text()
b = widgets.Button(
    description='get smiley',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Click me',
    icon='check'
)



def handle_submit(sender):
    with out:
        clear_output()
    with out:
        pred = clf.predict(vectorizer.transform([t.value]))
        
        display(Markdown("# " + str(sent2emoji(pred, lookup_emojis))))

b.on_click(handle_submit)
    
display(t)
display(widgets.VBox([b, out]))  

Text(value='')

In [ ]:
import numpy as np

y_trans = mlb.inverse_transform(yt1)
pred_trans = mlb.inverse_transform(yt1)

# evaluate accuracy
pos = 0
neg = 0
all = 0
for entry in range(len(y_trans)):
    if len(np.intersect1d(y_trans[entry], pred_trans[entry])) > 0:
        pos += 1
    else:
        neg += 1
    all += 1
print(pos/all)
print(neg)